In [7]:
import pandas as pd
import plotly.express as px

# Configuration
DATASET_URL = "https://www.kaggle.com/api/v1/datasets/download/mohammadehsani/student-performance-at-open-university"
DATA_DIR = "./data"
REQUIRED_FILES = [
    "courses.csv",
    "assessments.csv",
    "studentInfo.csv",
    "studentVle.csv",
    "studentAssessment.csv"
]

def load_data():
    # Define ordered categories
    result_order = ['Withdrawn', 'Fail', 'Pass', 'Distinction']
    age_band_order = ['0-35', '35-55', '55<=']
    imd_band_order = [
        '0-10%', '10-20%', '20-30%', '30-40%', 
        '40-50%', '50-60%', '60-70%', '70-80%', 
        '80-90%', '90-100%'
    ]
    
    # Load data with initial types
    data = {
        "courses": pd.read_csv(f"{DATA_DIR}/courses.csv"),
        "assessments": pd.read_csv(
            f"{DATA_DIR}/assessments.csv",
            dtype={
                'id_assessment': 'int32',
                'code_module': 'category',
                'code_presentation': 'category',
                'assessment_type': 'category', 
                'date': 'Int32'
            }
        ),
        "student_info": pd.read_csv(
            f"{DATA_DIR}/studentInfo.csv",
            dtype={
                'id_student': 'int32',
                'gender': 'category',
                'region': 'category',
                'highest_education': 'category',
                # 'disability': 'boolean'
            }
        ),
        "student_vle": pd.read_csv(
            f"{DATA_DIR}/studentVle.csv",
            dtype={'id_student': 'int32', 'sum_click': 'int16'}
        ),
        "student_assessment": pd.read_csv(
            f"{DATA_DIR}/studentAssessment.csv",
            dtype={'id_student': 'int32', 'score': 'float32'}
        )
    }

    # --- Assessment Date Imputation ---
    if 'date' in data["assessments"].columns:
        # Convert to numeric, coercing errors to NaN
        data["assessments"]['date'] = pd.to_numeric(data["assessments"]['date'], errors='coerce')
        
        # Calculate mean dates by assessment type
        mean_dates = data["assessments"].groupby('assessment_type')['date'].mean().round().astype('int32')
        
        # Impute missing dates with type-specific averages
        missing_dates = data["assessments"]['date'].isna()
        data["assessments"].loc[missing_dates, 'date'] = data["assessments"][missing_dates]['assessment_type'].map(mean_dates)

        
        # Convert to int32 after imputation
        data["assessments"]['date'] = data["assessments"]['date'].astype('int32')

    # --- Student Info Categorical Conversions ---
    data["student_info"]['final_result'] = pd.Categorical(
        data["student_info"]['final_result'],
        categories=result_order,
        ordered=True
    )
    
    data["student_info"]['age_band'] = pd.Categorical(
        data["student_info"]['age_band'],
        categories=age_band_order,
        ordered=True
    )
    
    data["student_info"]['imd_band'] = pd.Categorical(
        data["student_info"]['imd_band'],
        categories=imd_band_order,
        ordered=True
    )
    
    # Convert disability Y/N to boolean
    if 'disability' in data["student_info"].columns:
        data["student_info"]['disability'] = data["student_info"]['disability'].map({'Y': True, 'N': False})
    
    return data
if 'data' not in globals():
    data = load_data()
(
    courses,          # DataFrame with course/module info
    assessments,      # DataFrame with exam/assignment details
    student_info,     # DataFrame with student demographics and results
    student_vle,      # DataFrame with virtual learning environment interactions
    student_assessment # DataFrame with student scores for assessments
) = (
    data["courses"],
    data["assessments"],
    data["student_info"],
    data["student_vle"],
    data["student_assessment"]
)

In [8]:
courses.info()
assessments.info()
student_info.info()
student_vle.info()
student_assessment.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 22 entries, 0 to 21
Data columns (total 3 columns):
 #   Column                      Non-Null Count  Dtype 
---  ------                      --------------  ----- 
 0   code_module                 22 non-null     object
 1   code_presentation           22 non-null     object
 2   module_presentation_length  22 non-null     int64 
dtypes: int64(1), object(2)
memory usage: 660.0+ bytes
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 206 entries, 0 to 205
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype   
---  ------             --------------  -----   
 0   code_module        206 non-null    category
 1   code_presentation  206 non-null    category
 2   id_assessment      206 non-null    int32   
 3   assessment_type    206 non-null    category
 4   date               206 non-null    int32   
 5   weight             206 non-null    float64 
dtypes: category(3), float64(1), int32(2)
memory usage: 4.3 KB
<cla

In [9]:
import plotly.express as px

# 1. Convert categorical columns to strings (bypasses all issues)
plot_data = student_info[['gender', 'final_result']].copy()
plot_data['gender'] = plot_data['gender'].astype(str)
plot_data['final_result'] = plot_data['final_result'].astype(str)

# 2. Create the damn chart
fig = px.sunburst(
    plot_data,
    path=['gender', 'final_result'],
    color='final_result',
    color_discrete_map={
        'Withdrawn': '#FFC107',
        'Fail': '#F44336', 
        'Pass': '#4CAF50',
        'Distinction': '#2196F3'
    }
)

# 3. Show it
fig.show()

In [10]:
# 2. Age Band Distribution
age_data = student_info[['age_band', 'final_result']].copy()
age_data['age_band'] = age_data['age_band'].astype(str)
age_data['final_result'] = age_data['final_result'].astype(str)

fig2 = px.histogram(
    age_data,
    x='age_band',
    color='final_result',
    barmode='group',
    category_orders={
        'age_band': ['0-35', '35-55', '55<='],
        'final_result': ['Withdrawn', 'Fail', 'Pass', 'Distinction']
    },
    color_discrete_map={
        'Withdrawn': '#FFC107',
        'Fail': '#F44336', 
        'Pass': '#4CAF50',
        'Distinction': '#2196F3'
    },
    title='Age Distribution by Outcome'
)
fig2.show()

In [11]:
# 3. Assessment Scores by Type
if 'score' in student_assessment.columns:
    merged_scores = (
        assessments.merge(student_assessment, on='id_assessment')
        .merge(student_info[['id_student', 'gender']], on='id_student')
    )
    merged_scores['gender'] = merged_scores['gender'].astype(str)
    
    fig3 = px.box(
        merged_scores.dropna(subset=['score']),
        x='assessment_type',
        y='score',
        color='gender',
        points='all',
        title='Assessment Scores by Type and Gender'
    )
    fig3.show()
else:
    print("Score column not found in student_assessment DataFrame")

In [12]:
# 4. Engagement by Outcome
if 'sum_click' in student_vle.columns:
    engagement = (
        student_vle.merge(student_info[['id_student', 'final_result']], on='id_student')
        .groupby(['id_student', 'final_result'])['sum_click']
        .sum()
        .reset_index()
    )
    engagement['final_result'] = engagement['final_result'].astype(str)
    
    fig4 = px.box(
        engagement,
        x='final_result',
        y='sum_click',
        color='final_result',
        category_orders={
            'final_result': ['Withdrawn', 'Fail', 'Pass', 'Distinction']
        },
        color_discrete_map={
            'Withdrawn': '#FFC107',
            'Fail': '#F44336', 
            'Pass': '#4CAF50',
            'Distinction': '#2196F3'
        },
        title='VLE Engagement by Outcome'
    )
    fig4.show()

/tmp/ipykernel_121713/3555457464.py:5: FutureWarning:

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.

